# Lecture 9
Examples showing shape functions and mapppings 

Jim Brouzoulis

In [1]:
import numpy as np
import plotly.graph_objects as go

EDGE_COLOR = "black"
GRID_COLOR = "black"  # black wireframe grid lines
SURFACE_COLOR = "#1f77b4"  # requested color

# Elements covering [0,2]×[0,2]
elements = [
    (0.0, 1.0, 0.0, 1.0, "top-right"),    # E1
    (1.0, 2.0, 0.0, 1.0, "top-left"),     # E2
    (0.0, 1.0, 1.0, 2.0, "bottom-right"), # E3
    (1.0, 2.0, 1.0, 2.0, "bottom-left"),  # E4
]

def xi_eta(x, xmin, xmax):
    return 2.0*(x - xmin)/(xmax - xmin) - 1.0

def quad_corner_shape(xi, eta, corner):
    if corner == "bottom-left":   return 0.25*(1 - xi)*(1 - eta)
    if corner == "bottom-right":  return 0.25*(1 + xi)*(1 - eta)
    if corner == "top-right":     return 0.25*(1 + xi)*(1 + eta)
    if corner == "top-left":      return 0.25*(1 - xi)*(1 + eta)
    raise ValueError("Unknown corner name")

fig_hat_quad = go.Figure()

# Add surfaces and wireframe for each element
for (xmin, xmax, ymin, ymax, corner) in elements:
    nx, ny = 41, 41  # coarser grid for visible wireframe
    x = np.linspace(xmin, xmax, nx)
    y = np.linspace(ymin, ymax, ny)
    X, Y = np.meshgrid(x, y)
    XI = xi_eta(X, xmin, xmax)
    ET = xi_eta(Y, ymin, ymax)
    Z = quad_corner_shape(XI, ET, corner)

    # Surface with requested color and lighting
    fig_hat_quad.add_trace(go.Surface(
        x=X, y=Y, z=Z,
        surfacecolor=np.ones_like(Z),
        colorscale=[[0, SURFACE_COLOR], [1, SURFACE_COLOR]],
        showscale=False,
        opacity=0.9,
        name="Global hat",
        contours=dict(
            x=dict(show=True, color=GRID_COLOR, width=1, size=0.5),
            y=dict(show=True, color=GRID_COLOR, width=1, size=0.5),
            z=dict(show=False)
        ),
        lighting=dict(ambient=0.6, diffuse=0.6, specular=0.2),
        lightposition=dict(x=100, y=200, z=300)
    ))

    # Element edges (four corners)
    corners = [(xmin, ymin), (xmax, ymin), (xmax, ymax), (xmin, ymax)]
    for i in range(len(corners)):
        v0 = corners[i]
        v1 = corners[(i+1) % len(corners)]
        # Compute z at both points
        xi0, eta0 = xi_eta(v0[0], xmin, xmax), xi_eta(v0[1], ymin, ymax)
        xi1, eta1 = xi_eta(v1[0], xmin, xmax), xi_eta(v1[1], ymin, ymax)
        z0 = quad_corner_shape(xi0, eta0, corner)
        z1 = quad_corner_shape(xi1, eta1, corner)
        fig_hat_quad.add_trace(go.Scatter3d(
            x=[v0[0], v1[0]], y=[v0[1], v1[1]], z=[z0, z1],
            mode="lines",
            line=dict(color=EDGE_COLOR, width=6),
            showlegend=False
        ))

# Layout
fig_hat_quad.update_layout(
    title="Global Hat Function for bilinear approximation (four elements meeting)",
    width=700, height=560,
    margin=dict(l=20, r=20, t=60, b=20)
)

# Scene settings: uniform scale, no spikes
fig_hat_quad.update_scenes(
    xaxis=dict(title="x", range=[0, 2], showspikes=False),
    yaxis=dict(title="y", range=[0, 2], showspikes=False),
    zaxis=dict(title="N(x,y)", range=[0, 1], showspikes=False),
    aspectmode="cube"  # uniform scaling
)

fig_hat_quad.show()

In [2]:
# =========================================================
# Appearance settings
# =========================================================
GRID_COLOR   = "rgba(0,0,0,0.35)"   # wireframe grid lines on the surfaces
LINE_WIDTH   = 1.2
BASE_COLOR   = "#bbbbbb"            # base polygon fill (distinct from grid)
BASE_OPACITY = 0.50                 # more solid base (was 0.65)

# Shared color palette for shape functions
COLORS = {
    "N1": "#d62728",  # red
    "N2": "#1f77b4",  # blue
    "N3": "#ff7f0e",  # orange
    "N4": "#2ca02c",  # green
}

# =========================================================
# Helper: Constant-color Surface with structured wireframe
# =========================================================
def const_color_surface(x, y, z, color, name,
                        show_grid=True,
                        step_x=None, step_y=None,
                        line_color=GRID_COLOR, line_width=LINE_WIDTH):
    sc = np.ones_like(z)  # constant color
    trace = go.Surface(
        x=x, y=y, z=z, surfacecolor=sc,
        colorscale=[[0, color], [1, color]],
        showscale=False, opacity=1.0, name=name,
        # Hover: z-only (no x/y shown)
        hovertemplate="N=%{z:.3f}<extra></extra>"
    )
    if show_grid:
        xmin, xmax = np.nanmin(x), np.nanmax(x)
        ymin, ymax = np.nanmin(y), np.nanmax(y)
        # Defaults if not provided
        if step_x is None: step_x = max(0.20, (xmax - xmin) / 5.0)
        if step_y is None: step_y = max(0.20, (ymax - ymin) / 5.0)
        # Structured wireframe: x/y only
        trace.update(contours=dict(
            x=dict(show=True, color=line_color, width=line_width,
                   start=xmin, end=xmax, size=step_x),
            y=dict(show=True, color=line_color, width=line_width,
                   start=ymin, end=ymax, size=step_y),
            z=dict(show=False)  # no horizontal iso-lines
        ))
    trace.update(lighting=dict(ambient=0.6, diffuse=0.6, specular=0.2),
                 lightposition=dict(x=100, y=200, z=300))
    return trace
# =========================================================
# QUAD (Q4 / Melosh) — domain & shape functions
# =========================================================
m = 121
zeta = np.linspace(-1, 1, m)
eta  = np.linspace(-1, 1, m)
ZZ, EE = np.meshgrid(zeta, eta)

N1_rec = 0.25 * (1 - ZZ) * (1 - EE)
N2_rec = 0.25 * (1 + ZZ) * (1 - EE)
N3_rec = 0.25 * (1 + ZZ) * (1 + EE)
N4_rec = 0.25 * (1 - ZZ) * (1 + EE)

# =========================================================
# Quad overlay (all N1–N4 in one scene)
# =========================================================
fig_rec_overlay = go.Figure()
fig_rec_overlay.add_trace(const_color_surface(ZZ, EE, N1_rec, COLORS["N1"], "N1"))
fig_rec_overlay.add_trace(const_color_surface(ZZ, EE, N2_rec, COLORS["N2"], "N2"))
fig_rec_overlay.add_trace(const_color_surface(ZZ, EE, N3_rec, COLORS["N3"], "N3"))
fig_rec_overlay.add_trace(const_color_surface(ZZ, EE, N4_rec, COLORS["N4"], "N4"))
fig_rec_overlay.update_layout(
    title="Bilinear Rectangle — Overlay of N1, N2, N3, N4",
    width=650, height=520,
    margin=dict(l=20, r=20, t=60, b=20),
    legend=dict(orientation="h")
)
fig_rec_overlay.update_scenes(
    xaxis_title="ζ", yaxis_title="η", zaxis_title="N(ζ,η)",
    aspectmode="cube",
    xaxis=dict(range=[-1,1]), yaxis=dict(range=[-1,1]), zaxis=dict(range=[0,1])
)
fig_rec_overlay.show()

## The four bilinear shape functions for a quadrilateral element
These are vizualised over the parent domain in the natural coordinates ξ, η 

In [3]:
import numpy as np
import plotly.graph_objects as go

# =========================================================
# Appearance settings
# =========================================================
GRID_COLOR   = "black"              # wireframe grid lines on the surfaces
LINE_WIDTH   = 1.2
COLORS = {
    "N1": "#d62728",  # red
    "N2": "#1f77b4",  # blue
    "N3": "#ff7f0e",  # orange
    "N4": "#2ca02c",  # green
}

# =========================================================
# Helper: Constant-color Surface with structured wireframe
# =========================================================
def const_color_surface(x, y, z, color, name,
                        show_grid=True,
                        step_x=None, step_y=None,
                        line_color=GRID_COLOR, line_width=LINE_WIDTH):
    sc = np.ones_like(z)
    trace = go.Surface(
        x=x, y=y, z=z,
        surfacecolor=sc,
        colorscale=[[0, color], [1, color]],
        showscale=False,
        opacity=1.0,
        name=name,
        showlegend=True,
        hoverinfo="none",
        hovertemplate=f"{name}: %{{z:.3f}}<extra></extra>"
    )

    if show_grid:
        xmin, xmax = np.nanmin(x), np.nanmax(x)
        ymin, ymax = np.nanmin(y), np.nanmax(y)
        if step_x is None: step_x = max(0.20, (xmax - xmin) / 5.0)
        if step_y is None: step_y = max(0.20, (ymax - ymin) / 5.0)

        trace.update(contours=dict(
            x=dict(show=True, color=line_color, width=line_width,
                   start=xmin, end=xmax, size=step_x),
            y=dict(show=True, color=line_color, width=line_width,
                   start=ymin, end=ymax, size=step_y),
            z=dict(show=False)
        ))

    trace.update(lighting=dict(ambient=0.6, diffuse=0.6, specular=0.2),
                 lightposition=dict(x=100, y=200, z=300))
    return trace

# =========================================================
# QUAD (Q4) — domain & shape functions
# =========================================================
m = 121
zeta = np.linspace(-1, 1, m)
eta  = np.linspace(-1, 1, m)
ZZ, EE = np.meshgrid(zeta, eta)

N1_rec = 0.25 * (1 - ZZ) * (1 - EE)
N2_rec = 0.25 * (1 + ZZ) * (1 - EE)
N3_rec = 0.25 * (1 + ZZ) * (1 + EE)
N4_rec = 0.25 * (1 - ZZ) * (1 + EE)

# =========================================================
# Figure with overlay of shape functions
# =========================================================
fig_rec_overlay = go.Figure()

fig_rec_overlay.add_trace(const_color_surface(ZZ, EE, N1_rec, COLORS["N1"], "N1"))
fig_rec_overlay.add_trace(const_color_surface(ZZ, EE, N2_rec, COLORS["N2"], "N2"))
fig_rec_overlay.add_trace(const_color_surface(ZZ, EE, N3_rec, COLORS["N3"], "N3"))
fig_rec_overlay.add_trace(const_color_surface(ZZ, EE, N4_rec, COLORS["N4"], "N4"))

# Add solid black edges for the domain boundary
edges_x = [-1, 1, 1, -1, -1]
edges_y = [-1, -1, 1, 1, -1]
edges_z = [0, 0, 0, 0, 0]
fig_rec_overlay.add_trace(go.Scatter3d(
    x=edges_x, y=edges_y, z=edges_z,
    mode="lines",
    line=dict(color="black", width=6),
    name="Domain edges",
    showlegend=True
))

# Layout adjustments
fig_rec_overlay.update_layout(
    title="Bilinear Rectangle — Overlay of Shape Functions N1, N2, N3, N4",
    width=750, height=600,
    margin=dict(l=20, r=20, t=60, b=20),
    legend=dict(orientation="h", yanchor="top", y=1.25, xanchor="center", x=0.5),
    hovermode="closest",
    hoverlabel=dict(bgcolor="rgba(210,235,255,0.95)", font=dict(color="black"), bordercolor="royalblue"),
    scene_camera=dict(eye=dict(x=1.8, y=1.8, z=1.2))  # zoom out
)

# Scene: axis titles and ranges
fig_rec_overlay.update_scenes(
    xaxis=dict(title="ζ", range=[-1, 1], showspikes=False),
    yaxis=dict(title="η", range=[-1, 1], showspikes=False),
    zaxis=dict(title='', range=[0, 1], showspikes=False),  # remove rotated title
    aspectmode="manual",
    aspectratio=dict(x=1.2, y=1.2, z=0.8)
)

# Add horizontal annotation for z-axis meaning
fig_rec_overlay.add_annotation(
    text="N(ξ, η)",
    x=0.95, y=0.95,  # position near top-right
    xref="paper", yref="paper",
    showarrow=False,
    font=dict(size=14, color="black")
)

fig_rec_overlay.show()

## Example illustrating the bilinear approximation over one element with four DOFS

In [4]:
import numpy as np
import plotly.graph_objects as go

# -----------------------------
# Styling (same as your surfaces)
# -----------------------------
GRID_COLOR   = "rgba(0,0,0,0.35)"
LINE_WIDTH   = 1.2

def surface_u(xgrid, ygrid, ugrid, color, name,
              show_grid=True, step_x=None, step_y=None,
              line_color=GRID_COLOR, line_width=LINE_WIDTH):
    """Physical-space surface u(x,y) with x/y wireframe and minimal hover."""
    sc = np.ones_like(ugrid)
    trace = go.Surface(
        x=xgrid, y=ygrid, z=ugrid,
        surfacecolor=sc,
        colorscale=[[0, color], [1, color]],
        showscale=False, opacity=0.95,
        name=name, showlegend=True, legendgroup=name,
        hoverinfo="none",
        hovertemplate=f"{name}: %{{z:.3f}}<extra></extra>",
    )
    if show_grid:
        xmin, xmax = np.nanmin(xgrid), np.nanmax(xgrid)
        ymin, ymax = np.nanmin(ygrid), np.nanmax(ygrid)
        if step_x is None: step_x = max(0.25, (xmax - xmin)/6.0)
        if step_y is None: step_y = max(0.25, (ymax - ymin)/6.0)
        trace.update(contours=dict(
            x=dict(show=True, color=line_color, width=line_width,
                   start=xmin, end=xmax, size=step_x),
            y=dict(show=True, color=line_color, width=line_width,
                   start=ymin, end=ymax, size=step_y),
            z=dict(show=False)
        ))
    trace.update(lighting=dict(ambient=0.6, diffuse=0.6, specular=0.2),
                 lightposition=dict(x=100, y=200, z=300))
    return trace

# -----------------------------
# Naïve global bilinear interpolation for ONE Q4 element
# -----------------------------
def global_bilinear_element(xy_elem4, u_elem4, m=81):
    """
    Compute a naive global bilinear approximation u(x,y) on the element's AABB grid.
    Args
    ----
    xy_elem4 : (4,2) float array
        Element corner nodes in physical space (CCW: 1..4).
    u_elem4  : (4,) float array
        DOFs (nodal field values) [u1, u2, u3, u4].
    m : int
        Grid resolution per axis.
    Returns
    -------
    X, Y, U : (m,m) arrays
        Grid coordinates and approximated field on the element AABB.
    u_at_points : callable
        Function u_at_points(xp, yp) that returns u(xp, yp) for arrays/scalars.
    """
    xy = np.asarray(xy_elem4, dtype=float)
    u  = np.asarray(u_elem4,  dtype=float).ravel()
    assert xy.shape == (4,2), "Expect xy_elem4 to be (4,2)"
    assert u.shape  == (4,),  "Expect u_elem4 to be (4,)"

    xmin, xmax = np.min(xy[:,0]), np.max(xy[:,0])
    ymin, ymax = np.min(xy[:,1]), np.max(xy[:,1])

    xs = np.linspace(xmin, xmax, m)
    ys = np.linspace(ymin, ymax, m)
    X, Y = np.meshgrid(xs, ys)

    # normalize to [0,1]
    bx = (X - xmin) / (xmax - xmin + 1e-12)
    by = (Y - ymin) / (ymax - ymin + 1e-12)

    # rectangle bilinear shape functions
    N1 = (1 - bx) * (1 - by)
    N2 = bx * (1 - by)
    N3 = bx * by
    N4 = (1 - bx) * by
    U  = u[0]*N1 + u[1]*N2 + u[2]*N3 + u[3]*N4

    def u_at_points(xp, yp):
        xp = np.asarray(xp, dtype=float)
        yp = np.asarray(yp, dtype=float)
        bxp = (xp - xmin) / (xmax - xmin + 1e-12)
        byp = (yp - ymin) / (ymax - ymin + 1e-12)
        N1p = (1 - bxp) * (1 - byp)
        N2p = bxp * (1 - byp)
        N3p = bxp * byp
        N4p = (1 - bxp) * byp
        return u[0]*N1p + u[1]*N2p + u[2]*N3p + u[3]*N4p

    return X, Y, U, u_at_points

# -----------------------------
# Example: single element visualization (naïve only)
# -----------------------------
def show_single_naive(xy_elem4, u_elem4, color="#1f77b4", m=81):
    X, Y, U, _ = global_bilinear_element(xy_elem4, u_elem4, m=m)
    fig = go.Figure()
    fig.add_trace(surface_u(X, Y, U, color, "u (naïve global bilinear)", show_grid=True))
    fig.update_layout(
        title="Single Q4 element — naive global bilinear u(x,y) on AABB",
        width=760, height=540, margin=dict(l=24,r=24,t=56,b=24),
        legend=dict(orientation="h", yanchor="top", y=1.06, xanchor="center", x=0.5),
        hovermode="closest",
        hoverlabel=dict(bgcolor="rgba(210,235,255,0.95)", font=dict(color="black"), bordercolor="royalblue"),
    )
    fig.update_scenes(
        xaxis_title="x", yaxis_title="y", zaxis_title="uₕ",
        aspectmode="data",
        xaxis=dict(showspikes=False),
        yaxis=dict(showspikes=False),
        zaxis=dict(showspikes=False)
    )
    return fig

# --- Demo (edit freely) ---
if __name__ == "__main__":
    xy = np.array([[0.0,0.0],[2.4,0.1],[2.2,1.6],[0.0,1.4]])  # skewed quad
    u  = np.array([0.5, 1.0, 1.5, 2.0])
    fig = show_single_naive(xy, u, color="#1f77b4", m=81)
    fig.show()

## Example illustrating incompatible approximation
Using the naive approach with bilinear shape functions in global x-y only works if the shared edges are paralell with x and y.
Drag the sliders to to move the x coordinates to see the issue.

In [5]:
# Jupyter/VS Code single-cell demo:
# Two Q4 elements, separate plots:
#   1) Naïve global bilinear (evaluated on skewed geometry), with edge mismatch & node endpoints
#   2) Mapped isoparametric Q4 (geometry-aware), with edge mismatch & node endpoints
#
# Geometry controlled by sliders for two shared nodes.

import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

try:
    import ipywidgets as widgets
    from IPython.display import display
except Exception:
    widgets = None

# =========================================================
# Styling helpers
# =========================================================
GRID_COLOR = "rgba(0,0,0,0.35)"
LINE_WIDTH = 1.2

def surface_u(xgrid, ygrid, ugrid, color, name,
              show_grid=True, step_x=None, step_y=None,
              line_color=GRID_COLOR, line_width=LINE_WIDTH, opacity=0.95):
    """Physical-space surface u(x,y) with x/y wireframe and minimal hover."""
    sc = np.ones_like(ugrid)
    tr = go.Surface(
        x=xgrid, y=ygrid, z=ugrid,
        surfacecolor=sc,
        colorscale=[[0, color], [1, color]],
        showscale=False, opacity=opacity,
        name=name, showlegend=True,
        hoverinfo="none",
        hovertemplate=f"{name}: %{{z:.3f}}<extra></extra>",
    )
    if show_grid:
        xmin, xmax = np.nanmin(xgrid), np.nanmax(xgrid)
        ymin, ymax = np.nanmin(ygrid), np.nanmax(ygrid)
        if step_x is None: step_x = max(0.25, (xmax - xmin)/6.0)
        if step_y is None: step_y = max(0.25, (ymax - ymin)/6.0)
        tr.update(contours=dict(
            x=dict(show=True, color=line_color, width=line_width,
                   start=xmin, end=xmax, size=step_x),
            y=dict(show=True, color=line_color, width=line_width,
                   start=ymin, end=ymax, size=step_y),
            z=dict(show=False)
        ))
    tr.update(lighting=dict(ambient=0.6, diffuse=0.6, specular=0.2),
              lightposition=dict(x=100, y=200, z=300))
    return tr

def mesh_outline_traces(nodes6, node_size=11):
    """
    Build 2D traces (left subplot) for the two-element mesh:
    nodes6 order: [L1, L2(=R1), L3(=R4), L4, R2, R3]
    """
    L = np.vstack([nodes6[0], nodes6[1], nodes6[2], nodes6[3], nodes6[0]])  # close loop
    R = np.vstack([nodes6[1], nodes6[4], nodes6[5], nodes6[2], nodes6[1]])  # close loop
    traces = []
    traces.append(go.Scatter(
        x=L[:,0], y=L[:,1], mode="lines", name="Left element",
        line=dict(color="#1f77b4", width=3), showlegend=True, hoverinfo="skip"
    ))
    traces.append(go.Scatter(
        x=R[:,0], y=R[:,1], mode="lines", name="Right element",
        line=dict(color="#ff7f0e", width=3), showlegend=True, hoverinfo="skip"
    ))
    traces.append(go.Scatter(
        x=nodes6[:,0], y=nodes6[:,1], mode="markers+text",
        marker=dict(size=node_size, color="black"),
        text=[f"N{i+1}" for i in range(len(nodes6))],
        textposition="top center",
        name="Nodes", showlegend=True, hoverinfo="skip"
    ))
    return traces

# =========================================================
# Mapped Q4 routine (geometry + field via isoparametric shape functions)
# Corner order must be CCW: [BL, BR, TR, TL]
# =========================================================
def mapped_bilinear_element(xy_elem4, u_elem4, m=81):
    xy = np.asarray(xy_elem4, dtype=float)  # (4,2)
    u  = np.asarray(u_elem4,  dtype=float).ravel()  # (4,)
    assert xy.shape == (4,2)
    assert u.shape  == (4,)

    # Reference grid
    xis  = np.linspace(-1.0,  1.0, m)
    etas = np.linspace(-1.0,  1.0, m)
    XI, ETA = np.meshgrid(xis, etas)  # (m,m)

    # Q4 shape functions (BL, BR, TR, TL)
    def N_Q4(xi, eta):
        N1 = 0.25 * (1 - xi) * (1 - eta)  # BL
        N2 = 0.25 * (1 + xi) * (1 - eta)  # BR
        N3 = 0.25 * (1 + xi) * (1 + eta)  # TR
        N4 = 0.25 * (1 - xi) * (1 + eta)  # TL
        return np.stack([N1, N2, N3, N4], axis=0)  # (4, m, m)

    N = N_Q4(XI, ETA)
    X = np.sum(N * xy[:,0][:,None,None], axis=0)  # (m,m)
    Y = np.sum(N * xy[:,1][:,None,None], axis=0)  # (m,m)
    U = np.sum(N * u[:,None,None], axis=0)        # (m,m)

    # Edge parameterizations for shared edge
    # Left shared edge: xi = +1 | eta ∈ [-1,1] (between node 2 -> node 3)
    # Right shared edge: xi = -1 | eta ∈ [-1,1] (between node 1 -> node 4)
    def edge_left_xieta(etas):
        xi = +1.0
        eta = np.asarray(etas, dtype=float)
        N1 = 0.25 * (1 - xi) * (1 - eta)
        N2 = 0.25 * (1 + xi) * (1 - eta)
        N3 = 0.25 * (1 + xi) * (1 + eta)
        N4 = 0.25 * (1 - xi) * (1 + eta)
        x = xy[0,0]*N1 + xy[1,0]*N2 + xy[2,0]*N3 + xy[3,0]*N4
        y = xy[0,1]*N1 + xy[1,1]*N2 + xy[2,1]*N3 + xy[3,1]*N4
        u_edge = u[0]*N1 + u[1]*N2 + u[2]*N3 + u[3]*N4
        return x, y, u_edge

    def edge_right_xieta(etas):
        xi = -1.0
        eta = np.asarray(etas, dtype=float)
        N1 = 0.25 * (1 - xi) * (1 - eta)
        N2 = 0.25 * (1 + xi) * (1 - eta)
        N3 = 0.25 * (1 + xi) * (1 + eta)
        N4 = 0.25 * (1 - xi) * (1 + eta)
        x = xy[0,0]*N1 + xy[1,0]*N2 + xy[2,0]*N3 + xy[3,0]*N4
        y = xy[0,1]*N1 + xy[1,1]*N2 + xy[2,1]*N3 + xy[3,1]*N4
        u_edge = u[0]*N1 + u[1]*N2 + u[2]*N3 + u[3]*N4
        return x, y, u_edge

    return X, Y, U, edge_left_xieta, edge_right_xieta

# =========================================================
# Naïve global bilinear evaluated on PHYSICAL mapped grid
# IMPORTANT: This is NOT nodally exact on skewed quads.
# =========================================================
def naive_on_physical_grid(xy_elem4, u_elem4, X_phys, Y_phys):
    xy = np.asarray(xy_elem4, dtype=float)
    u  = np.asarray(u_elem4,  dtype=float).ravel()
    assert xy.shape == (4,2)
    assert u.shape  == (4,)

    xmin, xmax = np.min(xy[:,0]), np.max(xy[:,0])
    ymin, ymax = np.min(xy[:,1]), np.max(xy[:,1])

    bx = (X_phys - xmin) / (xmax - xmin + 1e-12)
    by = (Y_phys - ymin) / (ymax - ymin + 1e-12)

    N1 = (1 - bx) * (1 - by)  # BL
    N2 = bx * (1 - by)        # BR
    N3 = bx * by              # TR
    N4 = (1 - bx) * by        # TL

    U_naive = u[0]*N1 + u[1]*N2 + u[2]*N3 + u[3]*N4
    return U_naive

def naive_on_edge(xy_elem4, u_elem4, x_edge, y_edge):
    """Evaluate naïve field along a physical polyline (x_edge, y_edge)."""
    xy = np.asarray(xy_elem4, dtype=float)
    u  = np.asarray(u_elem4,  dtype=float).ravel()
    xmin, xmax = np.min(xy[:,0]), np.max(xy[:,0])
    ymin, ymax = np.min(xy[:,1]), np.max(xy[:,1])
    bxe = (x_edge - xmin) / (xmax - xmin + 1e-12)
    bye = (y_edge - ymin) / (ymax - ymin + 1e-12)
    N1e = (1 - bxe) * (1 - bye)
    N2e = bxe * (1 - bye)
    N3e = bxe * bye
    N4e = (1 - bxe) * bye
    return u[0]*N1e + u[1]*N2e + u[2]*N3e + u[3]*N4e

# =========================================================
# Build separate figures (Naïve and Mapped), each with mesh + surface + shared-edge curves
# =========================================================
def build_naive_figure(nodes6, dofs6, m=101, edge_samples=161):
    nodes6 = np.asarray(nodes6, dtype=float)
    dofs6  = np.asarray(dofs6,  dtype=float).ravel()
    # Element corners CCW: BL, BR, TR, TL
    L_xy = np.vstack([nodes6[0], nodes6[1], nodes6[2], nodes6[3]])
    R_xy = np.vstack([nodes6[1], nodes6[4], nodes6[5], nodes6[2]])
    L_u  = np.array([dofs6[0], dofs6[1], dofs6[2], dofs6[3]])
    R_u  = np.array([dofs6[1], dofs6[4], dofs6[5], dofs6[2]])

    # Use mapped geometry (without caring mapped u) to get physical grids
    XL, YL, _, edge_left_L, _  = mapped_bilinear_element(L_xy, L_u, m)
    XR, YR, _, _, edge_right_R = mapped_bilinear_element(R_xy, R_u, m)

    # Naïve surfaces evaluated on physical grids
    UL_naive = naive_on_physical_grid(L_xy, L_u, XL, YL)
    UR_naive = naive_on_physical_grid(R_xy, R_u, XR, YR)

    # Shared physical edge: take LEFT parameterization (xi=+1)
    et = np.linspace(-1.0, 1.0, edge_samples)
    xE_L, yE_L, _dummy = edge_left_L(et)

    # Force endpoints to be EXACT shared nodes (avoid tiny numerical drift)
    P = nodes6[1]  # shared A: L2 == R1
    Q = nodes6[2]  # shared B: L3 == R4
    xE_L[0], yE_L[0]   = P[0], P[1]
    xE_L[-1], yE_L[-1] = Q[0], Q[1]

    # Evaluate naïve u for BOTH elements along same physical polyline
    u_edge_L_naive = naive_on_edge(L_xy, L_u, xE_L, yE_L)
    u_edge_R_naive = naive_on_edge(R_xy, R_u, xE_L, yE_L)

    mismatch_edge = np.max(np.abs(u_edge_L_naive - u_edge_R_naive))
    mismatch_node_A = float(abs(u_edge_L_naive[0] - u_edge_R_naive[0]))
    mismatch_node_B = float(abs(u_edge_L_naive[-1] - u_edge_R_naive[-1]))

    # Figure
    fig = make_subplots(rows=1, cols=2,
                        specs=[[{"type":"xy"},{"type":"scene"}]],
                        subplot_titles=("Mesh geometry","Global bilinear"))
    for tr in mesh_outline_traces(nodes6): fig.add_trace(tr, row=1, col=1)
    fig.update_xaxes(title_text="x", row=1, col=1, zeroline=False, showgrid=True)
    fig.update_yaxes(title_text="y", row=1, col=1, zeroline=False, showgrid=True,
                     scaleanchor="x", scaleratio=1)

    fig.add_trace(surface_u(XL, YL, UL_naive, "#6baed6", "Left ", opacity=0.95), row=1, col=2)
    fig.add_trace(surface_u(XR, YR, UR_naive, "#e6550d", "Right ", opacity=0.95), row=1, col=2)

    # Edge curves (same x,y polyline, two different u-values)
    fig.add_trace(go.Scatter3d(
        x=xE_L, y=yE_L, z=u_edge_L_naive, mode="lines",
        line=dict(color="#000000", width=5), name="shared edge: Left)",
        hoverinfo="skip", showlegend=True), row=1, col=2)
    fig.add_trace(go.Scatter3d(
        x=xE_L, y=yE_L, z=u_edge_R_naive, mode="lines",
        line=dict(color="#000000", width=5, dash="solid"), name="shared edge: Right",
        hoverinfo="skip", showlegend=True), row=1, col=2)

    fig.update_layout(
        width=1100, height=650,
        margin=dict(l=30, r=30, t=90, b=30),
        legend=dict(orientation="h", yanchor="top", y=1.22, xanchor="center", x=0.5),
        hovermode="closest",
        hoverlabel=dict(bgcolor="rgba(210,235,255,0.95)", font=dict(color="black"), bordercolor="royalblue"),
        title=(f"Naïve approximation — max shared-edge mismatch = {mismatch_edge:.3e} "
               f"(nodes: A={mismatch_node_A:.3e}, B={mismatch_node_B:.3e})")
    )
    fig.update_scenes(xaxis_title="x", yaxis_title="y", zaxis_title="u",
                      aspectmode="data",
                      xaxis=dict(showspikes=False),
                      yaxis=dict(showspikes=False),
                      zaxis=dict(showspikes=False))
    return fig

def build_mapped_figure(nodes6, dofs6, m=101, edge_samples=161):
    nodes6 = np.asarray(nodes6, dtype=float)
    dofs6  = np.asarray(dofs6,  dtype=float).ravel()
    L_xy = np.vstack([nodes6[0], nodes6[1], nodes6[2], nodes6[3]])
    R_xy = np.vstack([nodes6[1], nodes6[4], nodes6[5], nodes6[2]])
    L_u  = np.array([dofs6[0], dofs6[1], dofs6[2], dofs6[3]])
    R_u  = np.array([dofs6[1], dofs6[4], dofs6[5], dofs6[2]])

    XL, YL, UL_map, edge_left_L, _  = mapped_bilinear_element(L_xy, L_u, m)
    XR, YR, UR_map, _, edge_right_R = mapped_bilinear_element(R_xy, R_u, m)

    # Shared physical edge parameterizations from mapped routines
    et = np.linspace(-1.0, 1.0, edge_samples)
    xE_L, yE_L, u_edge_L_map = edge_left_L(et)   # xi=+1
    xE_R, yE_R, u_edge_R_map = edge_right_R(et)  # xi=-1

    # Force endpoints to be EXACT shared nodes
    P = nodes6[1]  # shared A
    Q = nodes6[2]  # shared B
    xE_L[0], yE_L[0]   = P[0], P[1]
    xE_L[-1], yE_L[-1] = Q[0], Q[1]
    # Use LEFT polyline for plotting both curves to avoid tiny geometric drift
    mismatch_edge = np.max(np.abs(u_edge_L_map - u_edge_R_map))
    mismatch_node_A = float(abs(u_edge_L_map[0] - u_edge_R_map[0]))
    mismatch_node_B = float(abs(u_edge_L_map[-1] - u_edge_R_map[-1]))

    fig = make_subplots(rows=1, cols=2,
                        specs=[[{"type":"xy"},{"type":"scene"}]],
                        subplot_titles=("Mesh geometry","Mapped isoparametric Q4"))
    for tr in mesh_outline_traces(nodes6): fig.add_trace(tr, row=1, col=1)
    fig.update_xaxes(title_text="x", row=1, col=1, zeroline=False, showgrid=True)
    fig.update_yaxes(title_text="y", row=1, col=1, zeroline=False, showgrid=True,
                     scaleanchor="x", scaleratio=1)

    fig.add_trace(surface_u(XL, YL, UL_map, "#1f77b4", "Left (mapped)", opacity=0.95), row=1, col=2)
    fig.add_trace(surface_u(XR, YR, UR_map, "#ff7f0e", "Right (mapped)", opacity=0.95), row=1, col=2)

    # Edge curves (same x,y polyline; u from left/right mapped formulations)
    fig.add_trace(go.Scatter3d(
        x=xE_L, y=yE_L, z=u_edge_L_map, mode="lines",
        line=dict(color="black", width=5), name="shared edge: Left (mapped)",
        hoverinfo="skip", showlegend=True), row=1, col=2)
    fig.add_trace(go.Scatter3d(
        x=xE_L, y=yE_L, z=u_edge_R_map, mode="lines",
        line=dict(color="crimson", width=5, dash="dot"), name="shared edge: Right (mapped)",
        hoverinfo="skip", showlegend=True), row=1, col=2)

    fig.update_layout(
        width=1100, height=650,
        margin=dict(l=30, r=30, t=90, b=30),
        legend=dict(orientation="h", yanchor="top", y=1.3, xanchor="center", x=0.5),
        hovermode="closest",
        hoverlabel=dict(bgcolor="rgba(210,235,255,0.95)", font=dict(color="black"), bordercolor="royalblue"),
        title=(f"Mapped Q4 — max shared-edge mismatch = {mismatch_edge:.3e} "
               f"(nodes: A={mismatch_node_A:.3e}, B={mismatch_node_B:.3e})")
    )
    fig.update_scenes(xaxis_title="x", yaxis_title="y", zaxis_title="u",
                      aspectmode="data",
                      xaxis=dict(showspikes=False),
                      yaxis=dict(showspikes=False),
                      zaxis=dict(showspikes=False))
    return fig

# =========================================================
# Base geometry and DOFs
# =========================================================
nodes6_base = np.array([
    [0.0, 0.0],   # L1 (left bottom-left)
    [2.0, 0.0],   # L2 (= R1)  shared A (bottom-right)  <-- ABSOLUTE coords via sliders
    [2.0, 1.5],   # L3 (= R4)  shared B (top-right)     <-- ABSOLUTE coords via sliders
    [0.0, 1.5],   # L4 (left top-left)
    [4.0, 0.0],   # R2 (right bottom-right)
    [4.0, 1.5]    # R3 (right top-right)
], dtype=float)

# One DOF per unique node (edit freely)
dofs6 = np.array([0.5, 1.0, 2.0, 1.0, 2.2, 2.5], dtype=float)

# =========================================================
# Interactive or static
# =========================================================
if widgets is not None:
    xA = widgets.FloatSlider(value=nodes6_base[1,0], min=1.0, max=3.2, step=0.02, description="x(shared A)")
    yA = widgets.FloatSlider(value=nodes6_base[1,1], min=-0.5, max=1.5, step=0.02, description="y(shared A)")
    xB = widgets.FloatSlider(value=nodes6_base[2,0], min=1.0, max=3.2, step=0.02, description="x(shared B)")
    yB = widgets.FloatSlider(value=nodes6_base[2,1], min=0.2,  max=2.5, step=0.02, description="y(shared B)")
    dens = widgets.IntSlider(value=101, min=41, max=201, step=10, description="grid m")
    edge_n = widgets.IntSlider(value=161, min=41, max=401, step=20, description="edge samples")

    out = widgets.Output()

    def update_plot(*args):
        with out:
            out.clear_output(wait=True)
            nodes6 = nodes6_base.copy()
            nodes6[1] = [xA.value, yA.value]  # shared A (L2=R1)
            nodes6[2] = [xB.value, yB.value]  # shared B (L3=R4)

            fig_naive  = build_naive_figure(nodes6, dofs6, m=dens.value, edge_samples=edge_n.value)
            fig_mapped = build_mapped_figure(nodes6, dofs6, m=dens.value, edge_samples=edge_n.value)
            display(fig_naive)
            display(fig_mapped)

    for w in (xA, yA, xB, yB, dens, edge_n):
        w.observe(update_plot, names="value")

    display(widgets.VBox([
        widgets.HBox([xA, yA]),
        widgets.HBox([xB, yB]),
        widgets.HBox([dens, edge_n]),
    ]))
    update_plot()
    display(out)

else:
    fig_naive  = build_naive_figure(nodes6_base, dofs6, m=101, edge_samples=161)
    fig_mapped = build_mapped_figure(nodes6_base, dofs6, m=101, edge_samples=161)
    fig_naive.show()
    fig_mapped.show()

Output()

## Example of mapping a line to a line

In [6]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def plot_line_isoparametric(x1, x2, n_hover=201, hoverdistance=16,
                            hover_bg="rgba(210,235,255,0.95)", hover_font="black", hover_border="royalblue"):
    """
    Visualize a 1D isoparametric mapping with two linked panels:
      - Parent: ξ ∈ [-1, 1]
      - Mapped: line between x1 and x2 (1D or 2D coordinates)

    Hover over either panel to see the corresponding point highlighted in both.
    Works best in Jupyter/VS Code notebooks (FigureWidget callbacks).
    """
    # --- nodes ---
    x1 = np.array(x1, dtype=float).ravel()
    x2 = np.array(x2, dtype=float).ravel()
    dim = len(x1)
    if dim not in (1, 2):
        raise ValueError("x1/x2 must be 1D (scalar) or 2D (x,y).")

    # --- parent sampling & mapping (linear 1D element) ---
    xi_vals = np.linspace(-1.0, 1.0, n_hover)
    N1 = (1 - xi_vals) / 2.0
    N2 = (1 + xi_vals) / 2.0
    mapped = np.outer(N1, x1) + np.outer(N2, x2)  # (n_hover, dim)

    mapped_x = mapped[:, 0]
    mapped_y = mapped[:, 1] if dim == 2 else np.zeros_like(mapped_x)

    # --- build linked figure ---
    base = make_subplots(rows=1, cols=2,
                         subplot_titles=("Parent domain  [-1, 1]", "Mapped line"),
                         horizontal_spacing=0.08)
    fig = go.FigureWidget(base)

    # Parent line (visible line, no hover)
    fig.add_trace(go.Scatter(
        x=xi_vals, y=np.zeros_like(xi_vals),
        mode='lines',
        line=dict(color='black', width=3),
        hoverinfo='skip', showlegend=False
    ), row=1, col=1)

    # Parent hover points (almost invisible markers, with mapped coords in customdata)
    parent_custom = np.column_stack([mapped_x, mapped_y])  # (x,y) for tooltips
    fig.add_trace(go.Scatter(
        x=xi_vals, y=np.zeros_like(xi_vals),
        mode='markers',
        marker=dict(size=10, opacity=0.01, color='rgba(0,0,0,0)'),
        customdata=parent_custom,
        hovertemplate="ξ=%{x:.3f}<br>x=%{customdata[0]:.3f}" + ("<br>y=%{customdata[1]:.3f}" if dim==2 else "") + "<extra></extra>",
        showlegend=False
    ), row=1, col=1)
    idx_left_points = len(fig.data) - 1

    # Mapped line (visible line, no hover)
    fig.add_trace(go.Scatter(
        x=mapped_x, y=mapped_y,
        mode='lines',
        line=dict(color='black', width=3),
        hoverinfo='skip', showlegend=False
    ), row=1, col=2)

    # Mapped hover points (almost invisible, with ξ in customdata)
    mapped_custom = xi_vals  # store ξ
    fig.add_trace(go.Scatter(
        x=mapped_x, y=mapped_y,
        mode='markers',
        marker=dict(size=10, opacity=0.01, color='rgba(0,0,0,0)'),
        customdata=mapped_custom,
        hovertemplate="x=%{x:.3f}" + ("<br>y=%{y:.3f}" if dim==2 else "") + "<br>ξ=%{customdata:.3f}<extra></extra>",
        showlegend=False
    ), row=1, col=2)
    idx_right_points = len(fig.data) - 1

    # Hover highlights (red X)
    MARKER_SIZE = 18
    left_hover = go.Scatter(x=[], y=[], mode='markers',
                            marker=dict(size=MARKER_SIZE, color='crimson', symbol='x'),
                            hoverinfo='skip', showlegend=False)
    right_hover = go.Scatter(x=[], y=[], mode='markers',
                             marker=dict(size=MARKER_SIZE, color='crimson', symbol='x'),
                             hoverinfo='skip', showlegend=False)
    fig.add_trace(left_hover, row=1, col=1)
    fig.add_trace(right_hover, row=1, col=2)
    idx_left_hover  = len(fig.data) - 2
    idx_right_hover = len(fig.data) - 1

    # Axes & layout (same style as your 2D plots)
    fig.update_xaxes(title_text="ξ", range=[-1.05, 1.05], row=1, col=1, zeroline=False, showgrid=False)
    fig.update_yaxes(showticklabels=False, row=1, col=1)

    fig.update_xaxes(title_text="x", row=1, col=2, zeroline=False, showgrid=False)
    if dim == 2:
        fig.update_yaxes(title_text="y", row=1, col=2, zeroline=False, showgrid=False,
                         scaleanchor="x2", scaleratio=1)
    else:
        fig.update_yaxes(showticklabels=False, row=1, col=2)

    fig.update_layout(
        height=420, width=980,
        margin=dict(l=40, r=40, t=60, b=40),
        showlegend=False,
        plot_bgcolor='white', paper_bgcolor='white',
        hovermode='closest', hoverdistance=hoverdistance,
        hoverlabel=dict(bgcolor=hover_bg, font=dict(color=hover_font), bordercolor=hover_border)
    )

    # --- hover linkage (requires FigureWidget in notebook) ---
    def set_hover(i):
        if i is None or i < 0 or i >= len(xi_vals):
            # clear
            fig.data[idx_left_hover].x,  fig.data[idx_left_hover].y  = [], []
            fig.data[idx_right_hover].x, fig.data[idx_right_hover].y = [], []
            return
        xi = xi_vals[i]
        fig.data[idx_left_hover].x = [xi]
        fig.data[idx_left_hover].y = [0.0]
        fig.data[idx_right_hover].x = [mapped_x[i]]
        fig.data[idx_right_hover].y = [mapped_y[i]]

    def _on_hover_left(trace, points, state):
        if points.point_inds:
            set_hover(points.point_inds[0])

    def _on_unhover_left(trace, points, state):
        set_hover(None)

    def _on_hover_right(trace, points, state):
        if points.point_inds:
            set_hover(points.point_inds[0])

    def _on_unhover_right(trace, points, state):
        set_hover(None)

    # Attach callbacks
    fig.data[idx_left_points].on_hover(_on_hover_left)
    fig.data[idx_left_points].on_unhover(_on_unhover_left)
    fig.data[idx_right_points].on_hover(_on_hover_right)
    fig.data[idx_right_points].on_unhover(_on_unhover_right)

    return fig

# --- Examples ---
# 1D line from x1=0 to x2=10 (drawn along x-axis)
fig_1d = plot_line_isoparametric(x1=[-2], x2=[6])
fig_1d

# 2D line from (0,0) to (5,3) (slanted in 2D)
# fig_2d = plot_line_isoparametric(x1=[0,0], x2=[5,3])
# fig_2d

FigureWidget({
    'data': [{'hoverinfo': 'skip',
              'line': {'color': 'black', 'width': 3},
              'mode': 'lines',
              'showlegend': False,
              'type': 'scatter',
              'uid': 'ffffc0fe-0f21-4bf3-a7c7-a02658d0eb61',
              'x': {'bdata': ('AAAAAAAA8L+uR+F6FK7vv1yPwvUoXO' ... '/C9Shc7z+uR+F6FK7vPwAAAAAAAPA/'),
                    'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': ('AAAAAAAAAAAAAAAAAAAAAAAAAAAAAA' ... 'AAAAAAAAAAAAAAAAAAAAAAAAAAAAAA'),
                    'dtype': 'f8'},
              'yaxis': 'y'},
             {'customdata': {'bdata': ('AAAAAAAAAMAAAAAAAAAAAFyPwvUoXP' ... 'AAAAAAAAAAAAAAAAAYQAAAAAAAAAAA'),
                             'dtype': 'f8',
                             'shape': '201, 2'},
              'hovertemplate': 'ξ=%{x:.3f}<br>x=%{customdata[0]:.3f}<extra></extra>',
              'marker': {'color': 'rgba(0,0,0,0)', 'opacity': 0.01, 'size': 10},
              'mode': 'markers',